In [33]:
import pandas as pd
import requests, zipfile, io
import re
from datetime import datetime
import numpy as np



In [34]:

# Path to IGRA2 station list
station_list_path = "./data/IGRA/igra2-station-list.txt"

In [35]:


# Read as whitespace-delimited file
stations = pd.read_csv(
    station_list_path,
    delim_whitespace=True,
    header=None,
    usecols=[0,1,2,3,4,5,6],
    names=["id", "lat", "lon", "elev_m", "name1", "name2", "name3"],
    engine="python"
)

# The station name may be split across multiple columns, so join them
stations["name"] = stations[["name1","name2","name3"]].fillna("").agg(" ".join, axis=1).str.strip()

# Keep only relevant columns
stations = stations[["id","lat","lon","elev_m","name"]]


/var/folders/wb/w8f2wd_517gdp8khx2rp4pl00000gp/T/ipykernel_72229/1844851236.py:2: FutureWarning: The 'delim_whitespace' keyword in pd.read_csv is deprecated and will be removed in a future version. Use ``sep='\s+'`` instead
  stations = pd.read_csv(


In [36]:
stations


id      lat       lon  elev_m                      name
0     ACM00078861  17.1170  -61.7830    10.0       COOLIDGE FIELD (UA)
1     AEM00041217  24.4333   54.6500    16.0   ABU DHABI INTERNATIONAL
2     AEXUAE05467  25.2500   55.3700     4.0         SHARJAH 1935 1942
3     AFM00040911  36.7000   67.2000   378.0  MAZAR-I-SHARIF 2010 2014
4     AFM00040913  36.6667   68.9167   433.0          KUNDUZ 2010 2013
...           ...      ...       ...     ...                       ...
2918  ZZXUAICE022 -98.8888 -998.8888  -998.8            NP22 1974 1982
2919  ZZXUAICE026 -98.8888 -998.8888  -998.8            NP26 1983 1986
2920  ZZXUAICE028 -98.8888 -998.8888  -998.8            NP28 1986 1988
2921  ZZXUAICE030 -98.8888 -998.8888  -998.8            NP30 1988 1990
2922  ZZXUAICE031 -98.8888 -998.8888  -998.8            NP31 1989 1991

[2923 rows x 5 columns]

In [37]:

# Filter MJO box: 65E–120E, 10S–10N
mjo_stations = stations[
    (stations["lon"] >= 65) & (stations["lon"] <= 160) &
    (stations["lat"] >= -5) & (stations["lat"] <= 5)
].reset_index(drop=True)

mjo_stations

id     lat       lon  elev_m                           name
0   BXM00096315  4.9333  114.9333    22.0            BRUNEI AIRPORT 1981
1   BXM00096323  4.5830  114.2000     3.0              KUALA BELAIT 1999
2   CHM00056029  0.0033   96.9667  3716.9           YUSHU (56029-0) 1959
3   CHM00056080  0.0035  102.9000  2910.0                HEZUO 1960 2025
4   FMM00091434  1.0830  154.7670     3.0       KAPINGAMARANGI ATOL 1958
..          ...     ...       ...     ...                            ...
64  PPM00092044 -2.0500  147.4167     4.0               MOMOTE W.O. 1950
65  PPM00094076 -2.5670  150.8170     7.0         USAF-DS3-656 1992 1994
66  PPM00094085 -4.2170  152.1830     9.0         USAF-DS3-657 1950 1988
67  RSM00031770  0.0049  140.3000    20.5          SOVETSKAYA GAVAN 1964
68  SNM00048698  1.3679  103.9824    14.0  SINGAPORE/CHANGI AIRPORT 1955

[69 rows x 5 columns]

In [38]:

# Suppose you've already built mjo_stations
station = mjo_stations.iloc[0]
station_id = station["id"]

print("Downloading:", station_id, station["name"])

# Build URL
url = f"https://www.ncei.noaa.gov/pub/data/igra/data/data-por/{station_id}-data.txt.zip"
print(url)

# Download and unzip
r = requests.get(url)
z = zipfile.ZipFile(io.BytesIO(r.content))
fname = z.namelist()[0]

# Read lines
lines = z.read(fname).decode("utf-8").splitlines()
print("Number of lines:", len(lines))
print("First few lines:\n", "\n".join(lines[:15]))

Downloading: BXM00096315 BRUNEI AIRPORT 1981
https://www.ncei.noaa.gov/pub/data/igra/data/data-por/BXM00096315-data.txt.zip
Number of lines: 1550218
First few lines:
 #BXM00096315 1981 01 01 12 9999    3          usaf-ds3   49333  1149333
30 -9999  -9999   300 -9999 -9999 -9999     0    30 
30 -9999  -9999   600 -9999 -9999 -9999   350    25 
30 -9999  -9999   900 -9999 -9999 -9999   335    20 
#BXM00096315 1981 01 02 00 9999    3          usaf-ds3   49333  1149333
30 -9999  -9999   300 -9999 -9999 -9999   170    25 
30 -9999  -9999   600 -9999 -9999 -9999    90     5 
30 -9999  -9999  2400 -9999 -9999 -9999   100    30 
#BXM00096315 1981 01 04 12 9999    5          usaf-ds3   49333  1149333
31 -9999  -9999     5 -9999 -9999 -9999   210    30 
30 -9999  -9999   300 -9999 -9999 -9999   215   103 
30 -9999  -9999   600 -9999 -9999 -9999   230    41 
30 -9999  -9999   900 -9999 -9999 -9999   230    82 
30 -9999  -9999  1500 -9999 -9999 -9999   230    51 
#BXM00096315 1981 01 05 00 9999   

In [39]:
type(lines)

list

In [40]:
len(lines)

1550218

In [53]:
import re
from datetime import datetime
import pandas as pd
import numpy as np

QC_LETTER_RE = re.compile(r'[A-Za-z]')

def _to_num(token: str, scale=1.0, missing=-9999, allow_signed=True):
    if token is None:
        return np.nan
    t = QC_LETTER_RE.sub('', token.strip())
    if t == '':
        return np.nan
    try:
        val = int(t) if allow_signed else int(t.replace('-', ''))
    except ValueError:
        return np.nan
    if val == missing:
        return np.nan
    return val / scale

def parse_header(header_line: str):
    stn_id   = header_line[1:12].strip()
    year     = int(header_line[13:17])
    month    = int(header_line[18:20])
    day      = int(header_line[21:23])
    hour     = int(header_line[24:26])
    ts = pd.Timestamp(datetime(year, month, day, hour))
    try:
        approx_levels = int(header_line[27:31].strip())
    except Exception:
        approx_levels = None
    return stn_id, ts, approx_levels

def parse_level_line(ln: str) -> dict:
    return {
        "level_type":     _to_num(ln[0:2],   scale=1.0,  missing=-9999, allow_signed=False),
        "pressure_hPa":   _to_num(ln[10:17], scale=10.0),
        "height_m":       _to_num(ln[17:24], scale=1.0),
        "temp_C":         _to_num(ln[24:31], scale=10.0),
        "dewpoint_C":     _to_num(ln[31:38], scale=10.0),
        "rh_pct":         _to_num(ln[38:43], scale=1.0),
        "wind_dir_deg":   _to_num(ln[43:49], scale=1.0),
        "wind_speed_mps": _to_num(ln[49:55], scale=10.0),
    }

def split_into_soundings(lines: list[str]):
    soundings = []
    cur_header, cur_levels = None, []
    def flush():
        nonlocal cur_header, cur_levels
        if cur_header is not None and cur_levels:
            soundings.append((cur_header, cur_levels))
        cur_header, cur_levels = None, []
    for ln in lines:
        if not ln.strip():
            continue
        if ln.startswith('#'):
            flush()
            cur_header = ln
        else:
            cur_levels.append(ln)
    flush()
    return soundings

def build_catalog_and_metadata(lines: list[str], drop_empty: bool = True):
    """
    Returns:
      catalog: dict[catalog_key -> DataFrame]
      meta:    DataFrame with per-sounding stats (includes 'catalog_key' and 'status')
    If drop_empty=True, both outputs exclude soundings classified as 'empty'.
    """
    soundings = split_into_soundings(lines)
    catalog = {}
    meta_rows = []

    # handle duplicate timestamps by suffixing keys
    duplicates_count: dict[pd.Timestamp, int] = {}

    for header, level_lines in soundings:
        stn_id, ts, approx_count = parse_header(header)
        rows = [parse_level_line(ln) for ln in level_lines]
        df = pd.DataFrame(rows)
        df.insert(0, "station", stn_id)
        df.insert(1, "time", ts)

        # classify BEFORE dropping anything
        n_valid_pres = int(df["pressure_hPa"].notna().sum())
        n_valid_temp = int(df["temp_C"].notna().sum())
        n_valid_wind = int(df["wind_speed_mps"].notna().sum())

        if n_valid_pres == 0 and n_valid_temp == 0 and n_valid_wind == 0:
            status = "empty"
        elif n_valid_pres == 0 and n_valid_temp == 0 and n_valid_wind > 0:
            status = "winds_only"
        elif n_valid_temp == 0 and n_valid_pres > 0:
            status = "pressure_only"
        else:
            status = "full"

        # now drop rows that are completely useless across all key fields
        df = df.dropna(
            how="all",
            subset=["pressure_hPa","height_m","temp_C","dewpoint_C","wind_dir_deg","wind_speed_mps"]
        ).reset_index(drop=True)

        # sort by pressure if present; else by height if present
        if df["pressure_hPa"].notna().any():
            df = df.sort_values("pressure_hPa", ascending=False).reset_index(drop=True)
        elif df["height_m"].notna().any():
            df = df.sort_values("height_m", ascending=True).reset_index(drop=True)

        # unique catalog key (timestamp + optional suffix)
        if ts in duplicates_count:
            duplicates_count[ts] += 1
            key = f"{ts.isoformat()}.{duplicates_count[ts]}"
        else:
            duplicates_count[ts] = 1
            key = ts.isoformat()

        # store even if empty for now; we'll filter at the end if requested
        catalog[key] = df

        # compute simple stats from the (lightly) cleaned df
        n_levels = len(df)
        p_max = float(df["pressure_hPa"].max()) if df["pressure_hPa"].notna().any() else np.nan
        p_min = float(df["pressure_hPa"].min()) if df["pressure_hPa"].notna().any() else np.nan
        z_top = float(df["height_m"].max()) if df["height_m"].notna().any() else np.nan

        meta_rows.append({
            "catalog_key": key,
            "station": stn_id,
            "time": ts,
            "status": status,
            "approx_levels_header": approx_count,
            "n_levels": n_levels,
            "n_valid_pressure": n_valid_pres,
            "n_valid_temp": n_valid_temp,
            "n_valid_wind": n_valid_wind,
            "p_max_hPa_surface": p_max,
            "p_min_hPa_top": p_min,
            "z_top_m": z_top,
        })

    meta = pd.DataFrame(meta_rows).sort_values("time").reset_index(drop=True)

    if drop_empty:
        # keep only non-empty in meta
        meta = meta[meta["status"] != "empty"].reset_index(drop=True)
        # align catalog to filtered meta
        keep_keys = set(meta["catalog_key"])
        catalog = {k: v for k, v in catalog.items() if k in keep_keys}

    return catalog, meta


In [54]:

catalog, meta = build_catalog_and_metadata(lines, drop_empty=True)


In [56]:
print(meta["status"].value_counts())
print(f"Catalog size: {len(catalog)}  |  Meta rows: {len(meta)}")

status
winds_only       28888
pressure_only    20790
full               919
Name: count, dtype: int64
Catalog size: 50597  |  Meta rows: 50597


In [55]:

meta        

catalog_key      station                time      status  \
0      1981-01-01T12:00:00  BXM00096315 1981-01-01 12:00:00  winds_only   
1      1981-01-02T00:00:00  BXM00096315 1981-01-02 00:00:00  winds_only   
2      1981-01-04T12:00:00  BXM00096315 1981-01-04 12:00:00  winds_only   
3      1981-01-05T00:00:00  BXM00096315 1981-01-05 00:00:00  winds_only   
4      1981-01-06T06:00:00  BXM00096315 1981-01-06 06:00:00  winds_only   
...                    ...          ...                 ...         ...   
50592  2025-08-23T12:00:00  BXM00096315 2025-08-23 12:00:00  winds_only   
50593  2025-08-23T18:00:00  BXM00096315 2025-08-23 18:00:00  winds_only   
50594  2025-08-24T06:00:00  BXM00096315 2025-08-24 06:00:00  winds_only   
50595  2025-08-24T12:00:00  BXM00096315 2025-08-24 12:00:00  winds_only   
50596  2025-08-24T18:00:00  BXM00096315 2025-08-24 18:00:00  winds_only   

       approx_levels_header  n_levels  n_valid_pressure  n_valid_temp  \
0                      9999         3                 0             0   
1                      9999         3                 0             0   
2                      9999         5                 0             0   
3                      9999         4                 0             0   
4                      9999         5                 0             0   
...                     ...       ...               ...           ...   
50592                  9999         5                 0             0   
50593                  9999         5                 0             0   
50594                  9999         3                 0             0   
50595                  9999         5                 0             0   
50596                  9999         5                 0             0   

       n_valid_wind  p_max_hPa_surface  p_min_hPa_top  z_top_m  
0                 3                NaN            NaN      NaN  
1                 3                NaN            NaN      NaN  
2                 5                NaN            NaN      NaN  
3                 4                NaN            NaN      NaN  
4                 5                NaN            NaN      NaN  
...             ...                ...            ...      ...  
50592             5                NaN            NaN      NaN  
50593             5                NaN            NaN      NaN  
50594             3                NaN            NaN      NaN  
50595             5                NaN            NaN      NaN  
50596             5                NaN            NaN      NaN  

[50597 rows x 12 columns]

In [57]:
print(len(catalog), "soundings parsed")

50597 soundings parsed


In [58]:
catalog

{'1981-01-01T12:00:00':        station                time  level_type  pressure_hPa  height_m  \
 0  BXM00096315 1981-01-01 12:00:00        30.0           NaN       NaN   
 1  BXM00096315 1981-01-01 12:00:00        30.0           NaN       NaN   
 2  BXM00096315 1981-01-01 12:00:00        30.0           NaN       NaN   
 
    temp_C  dewpoint_C  rh_pct  wind_dir_deg  wind_speed_mps  
 0     NaN         NaN     9.0           0.0             3.0  
 1     NaN         NaN     NaN          50.0             2.5  
 2     NaN         NaN     NaN          35.0             2.0  ,
 '1981-01-02T00:00:00':        station       time  level_type  pressure_hPa  height_m  temp_C  \
 0  BXM00096315 1981-01-02        30.0           NaN       NaN     NaN   
 1  BXM00096315 1981-01-02        30.0           NaN       NaN     NaN   
 2  BXM00096315 1981-01-02        30.0           NaN       NaN     NaN   
 
    dewpoint_C  rh_pct  wind_dir_deg  wind_speed_mps  
 0         NaN     NaN          70.0          

In [59]:
type(catalog)

dict

In [61]:
# Filter meta for full soundings only
meta_full = meta[meta["status"] == "full"].reset_index(drop=True)

# Build a new catalog with only those keys
catalog_full = {k: catalog[k] for k in meta_full["catalog_key"]}

print(f"Original catalog: {len(catalog)} soundings")
print(f"Full-only subset: {len(catalog_full)} soundings")

# Quick check
print(meta_full.head())
example_key = meta_full.loc[0, "catalog_key"]
print(catalog_full[example_key].head())


Original catalog: 50597 soundings
Full-only subset: 919 soundings
           catalog_key      station                time status  \
0  1990-01-02T00:00:00  BXM00096315 1990-01-02 00:00:00   full   
1  1990-01-15T12:00:00  BXM00096315 1990-01-15 12:00:00   full   
2  1990-01-22T12:00:00  BXM00096315 1990-01-22 12:00:00   full   
3  1990-01-23T12:00:00  BXM00096315 1990-01-23 12:00:00   full   
4  1990-01-24T00:00:00  BXM00096315 1990-01-24 00:00:00   full   

   approx_levels_header  n_levels  n_valid_pressure  n_valid_temp  \
0                  9999        12                 7             3   
1                  9999        32                 7             1   
2                  9999        44                 7             1   
3                  9999        10                 7             1   
4                  9999        28                 0             2   

   n_valid_wind  p_max_hPa_surface  p_min_hPa_top  z_top_m  
0            12             8500.0            0.0   5850.0  


In [62]:
meta_full

catalog_key      station                time status  \
0    1990-01-02T00:00:00  BXM00096315 1990-01-02 00:00:00   full   
1    1990-01-15T12:00:00  BXM00096315 1990-01-15 12:00:00   full   
2    1990-01-22T12:00:00  BXM00096315 1990-01-22 12:00:00   full   
3    1990-01-23T12:00:00  BXM00096315 1990-01-23 12:00:00   full   
4    1990-01-24T00:00:00  BXM00096315 1990-01-24 00:00:00   full   
..                   ...          ...                 ...    ...   
914  1993-10-29T00:00:00  BXM00096315 1993-10-29 00:00:00   full   
915  1993-10-29T12:00:00  BXM00096315 1993-10-29 12:00:00   full   
916  1993-10-30T00:00:00  BXM00096315 1993-10-30 00:00:00   full   
917  1993-10-30T12:00:00  BXM00096315 1993-10-30 12:00:00   full   
918  1993-10-31T00:00:00  BXM00096315 1993-10-31 00:00:00   full   

     approx_levels_header  n_levels  n_valid_pressure  n_valid_temp  \
0                    9999        12                 7             3   
1                    9999        32                 7             1   
2                    9999        44                 7             1   
3                    9999        10                 7             1   
4                    9999        28                 0             2   
..                    ...       ...               ...           ...   
914                  9999        13                 7             1   
915                  9999        25                 0             4   
916                  9999        34                 7             1   
917                  9999        39                 7             4   
918                  9999        13                 7             2   

     n_valid_wind  p_max_hPa_surface  p_min_hPa_top  z_top_m  
0              12             8500.0            0.0   5850.0  
1              32             8500.0            0.0   9999.0  
2              44             8500.0            0.0   9999.0  
3              10             8500.0            0.0   5830.0  
4              28                NaN            NaN   9999.0  
..            ...                ...            ...      ...  
914            13             8500.0            0.0   5860.0  
915            25                NaN            NaN   9999.0  
916            34             8500.0            0.0   9999.0  
917            39             8500.0            0.0   9999.0  
918            13             8500.0            0.0   5850.0  

[919 rows x 12 columns]

In [63]:
catalog_full

{'1990-01-02T00:00:00':         station       time  level_type  pressure_hPa  height_m  temp_C  \
 0   BXM00096315 1990-01-02        10.0        8500.0    1497.0     NaN   
 1   BXM00096315 1990-01-02        10.0        7000.0    3131.0     NaN   
 2   BXM00096315 1990-01-02        10.0        5000.0    5850.0    -4.3   
 3   BXM00096315 1990-01-02        10.0        4000.0       NaN    17.1   
 4   BXM00096315 1990-01-02        10.0        3000.0       NaN    30.3   
 5   BXM00096315 1990-01-02        21.0          40.0      15.0     NaN   
 6   BXM00096315 1990-01-02        10.0           0.0      85.0     NaN   
 7   BXM00096315 1990-01-02        10.0           NaN       NaN     NaN   
 8   BXM00096315 1990-01-02        10.0           NaN       NaN     NaN   
 9   BXM00096315 1990-01-02        10.0           NaN       NaN     NaN   
 10  BXM00096315 1990-01-02        22.0           NaN       NaN     NaN   
 11  BXM00096315 1990-01-02        10.0           NaN       NaN     NaN   
 


In [ ]:
import plotly.express as px

# Pick one sounding (first entry in the dict)
key, df = next(iter(catalog_full.items()))

# df has columns like ["station","time","level_type","pressure_hPa","height_m","temp_C",...]

# Make a temperature vs. pressure plot (log-y axis, inverted so surface is at bottom)
fig = px.line(
    df,
    x="temp_C",
    y="pressure_hPa",
    markers=True,
    title=f"Sounding at {key} (Station {df['station'].iloc[0]})",
    labels={"temp_C": "Temperature (°C)", "pressure_hPa": "Pressure (hPa)"}
)

# Reverse y-axis so surface (1000 hPa) is at bottom
fig.update_yaxes(autorange="reversed", type="log", range=[3, 3])  # auto log scale

fig.update_layout(
    yaxis=dict(scaleanchor="x", scaleratio=5),  # make vertical stretch adjustable
    width=500,
    height=700,
)

fig.show()


SyntaxError: invalid syntax. Perhaps you forgot a comma? (876399908.py, line 4)